# Import Libraries

In [ ]:
### imports libraries & setup
RANDOM_SEED = 42

import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
os.environ['PYTHONHASHSEED'] = str(RANDOM_SEED)
os.environ['MPLCONFIGDIR'] = os.getcwd()+'/configs/'

import random
random.seed(RANDOM_SEED)

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=Warning)

import logging

import math

import numpy as np
np.random.seed(RANDOM_SEED)

import tensorflow as tf
from tensorflow import keras as tfk
from tensorflow.keras import layers as tfkl
tf.autograph.set_verbosity(0)
tf.get_logger().setLevel(logging.ERROR)
tf.compat.v1.logging.set_verbosity(tf.compat.v1.logging.ERROR)
tf.random.set_seed(RANDOM_SEED)
tf.compat.v1.set_random_seed(RANDOM_SEED)

import pandas as pd

import matplotlib as mpl
import matplotlib.pyplot as plt

import seaborn as sns

from sklearn.model_selection import train_test_split, KFold
from sklearn.metrics import mean_squared_error

import re

import zipfile

### cd into the script directory
from google.colab import drive
drive.mount('/content/drive')
os.chdir(HOMEWORK1_PATH)

### plots a grid of images
def plot_images(
  images:      list,                # images to display
  captions:    list[str],           # caption of each image
  num_of_cols: int=5,               # number of images per each row
  image_size:  tuple[int]=(3, 3),   # size of each image in inches
):

  num_of_rows = math.ceil(len(images) / num_of_cols)
  fig_size = (image_size[0]*num_of_cols, image_size[1]*num_of_rows)

  fig, axes = plt.subplots(
    nrows=num_of_rows,
    ncols=num_of_cols,
    figsize=fig_size,
  )

  axes = axes.flatten()

  for i in range(num_of_cols*num_of_rows):
    ax = axes[i]

    # disable axis
    ax.axis('off')

    # show the image
    if i < len(images):
      ax.imshow(images[i])
      ax.set_title(captions[i])

  plt.tight_layout()
  plt.show()

  ### finds all images that are similar to a given reference image
def index_of_similar_images(
  reference,          # image to search
  images,             # array if images
  threshold: float,   # value from 0 to 1 (the closer to 1, the more similar)
):

  from skimage.metrics import structural_similarity as ssim
  from skimage.transform import resize

  # evaluates the similarity score for each image
  similarity_scores = []
  for image in images:
    # resizes the reference image to match the dimensions of the current image
    resized_reference = resize(reference, image.shape, anti_aliasing=True, mode='reflect')
    score = ssim(image, resized_reference, multichannel=True)
    similarity_scores.append(score)

  similarity_scores = np.array(similarity_scores)

  # indexes of scores that are larger than the threshold
  indexes = np.where(similarity_scores >= threshold)[0]

  # sorts the indexes by the corresponding values
  sorted_indexes = indexes[np.argsort(similarity_scores[indexes])]

  return sorted_indexes

clean_data = np.load(HOMEWORK1_PATH+'/clean_data.npy')
clean_labels = np.load(HOMEWORK1_PATH+'/clean_labels.npy', allow_pickle = True)

### one-hot encode labels
mapping = {
  'healthy': 0,
  'unhealthy': 1,
}

# maps labels according do the mapping
vfunc = np.vectorize(lambda label: mapping[label])

encoded_labels = tf.keras.utils.to_categorical(
  vfunc(clean_labels),
  num_classes=2,
  dtype='float32'
)
encoded_labels[0:10]

augment = tf.keras.Sequential([
  #tfkl.RandomZoom(height_factor = 0.1152,width_factor=0.1152,fill_mode='reflect',interpolation='bilinear'),
  tfkl.RandomFlip("horizontal_and_vertical", seed=42),
  tfkl.RandomRotation(factor = (-1,1),fill_mode='reflect',interpolation='bilinear'),
  #tfkl.RandomBrightness(0.2, value_range=(0,1)),
  #tf.keras.layers.RandomContrast(factor = 0.3)
  ])

# Indici delle etichette 'healthy'
healthy_indices = np.where(encoded_labels[:, 0] == 1)[0]
unhealthy_indices = np.where(encoded_labels[:, 1] == 1)[0]

# Ora healthy_indices conterrà gli indici delle istanze corrispondenti alla classe 'healthy'
print(healthy_indices[0:10])

# Suddividi l'array data e label in base agli indici
clean_data_healthy = clean_data[healthy_indices]
clean_data_unhealthy = clean_data[unhealthy_indices]
clean_labels_healthy = encoded_labels[healthy_indices]
clean_labels_unhealthy = encoded_labels[unhealthy_indices]

print(f"lunghezza healthy = {len(clean_data_healthy)} e lunghezza unhealthy = {len(clean_data_unhealthy)}")
clean_data_healthy.shape

clean_data_healthy2=np.concatenate([clean_data_healthy, augment(clean_data_healthy[0:500])])
clean_data_unhealthy2=np.concatenate([clean_data_unhealthy, augment(clean_data_unhealthy[0:1700])])
clean_labels_healthy=np.concatenate([clean_labels_healthy, clean_labels_healthy[0:500]])
clean_labels_unhealthy=np.concatenate([clean_labels_unhealthy, clean_labels_unhealthy[0:1700]])
print(f"lunghezza healthy = {len(clean_data_healthy2)} e lunghezza unhealthy = {len(clean_data_unhealthy2)}")
print(f"lunghezza healthy = {len(clean_labels_healthy)} e lunghezza unhealthy = {len(clean_labels_unhealthy)}")

clean_data2=np.concatenate([clean_data_healthy2, clean_data_unhealthy2])
encoded_labels2=np.concatenate([clean_labels_healthy, clean_labels_unhealthy])
print(f"Shape data = {clean_data2.shape} e lunghezza labels = {encoded_labels2.shape}")

Mounted at /content/drive
[ 0  1  2  5  7  8  9 10 11 12]
lunghezza healthy = 3101 e lunghezza unhealthy = 1903
lunghezza healthy = 3601 e lunghezza unhealthy = 3603
lunghezza healthy = 3601 e lunghezza unhealthy = 3603
Shape data = (7204, 96, 96, 3) e lunghezza labels = (7204, 2)


## Processing

In [ ]:
### train, validation and test sets
VAL_PERCENTAGE  = 0.2

# uses more standard notation
x_train_val = clean_data2
y_train_val = encoded_labels2


# splits *_train_val_test into *_train_val and *_test
x_train, x_val, y_train, y_val = train_test_split(
  x_train_val,
  y_train_val,
  random_state=RANDOM_SEED,
  test_size=VAL_PERCENTAGE,
  stratify=np.argmax(y_train_val,axis=1)
)

# shows some stats
sizes = np.array([len(x_train), len(x_val)])
df = pd.DataFrame({
  'Set'  : ['train', 'val'],
  'Count': sizes,
  '%'    : (100 * sizes / sum(sizes)).round(2)
})

df

# Indici delle etichette 'healthy'
healthy_train_indices = np.where(y_train[:, 0] == 1)[0]
unhealthy_train_indices = np.where(y_train[:, 1] == 1)[0]
healthy_val_indices = np.where(y_val[:, 0] == 1)[0]
unhealthy_val_indices = np.where(y_val[:, 1] == 1)[0]
print(f"Numero di train healthy = {len(healthy_train_indices)} e di train unhealthy = {len(unhealthy_train_indices)}")
print(f"Numero di val healthy = {len(healthy_val_indices)} e di val unhealthy = {len(unhealthy_val_indices)}")

### input shape of the model
input_shape = x_train_val.shape[1:]
input_shape

Numero di train healthy = 2881 e di train unhealthy = 2882
Numero di val healthy = 720 e di val unhealthy = 721


(96, 96, 3)

# 3MOD_3 (VGG + VGG16 + UltraModel)

In [ ]:
mod1 = tfk.models.load_model('BalancedProcessed', custom_objects={'LeakyReLU': tfk.layers.LeakyReLU()}, compile=False)
mod1._name = 'balanced'
mod2 = tfk.models.load_model('Ultra', custom_objects={'LeakyReLU': tfk.layers.LeakyReLU()}, compile=False)
mod2._name = 'ultra'
mod3 = tfk.models.load_model('FineTuningModel_vgg3_test', custom_objects={'LeakyReLU': tfk.layers.LeakyReLU()}, compile=False)
mod3._name = 'vgg_test'

inputs = tfkl.Input(shape=input_shape)
out1 = mod1(tf.identity(inputs))
out2 = mod2(tf.identity(inputs))
out3 = mod3(tf.identity(inputs))
outputs = tfkl.Average()([out1, out2, out3])

model = tfk.Model(inputs=inputs, outputs=outputs, name='3Modelli')
model.compile(
    loss=tfk.losses.CategoricalCrossentropy(),
    optimizer=tfk.optimizers.Adam(),
    metrics=['Accuracy', 'Precision', 'Recall', 'F1Score']
)
model.summary()
tfk.utils.plot_model(model, expand_nested=True, show_shapes=True)

Model: "3Modelli"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 96, 96, 3)]          0         []                            
                                                                                                  
 tf.identity_1 (TFOpLambda)  (None, 96, 96, 3)            0         ['input_1[0][0]']             
                                                                                                  
 tf.identity_2 (TFOpLambda)  (None, 96, 96, 3)            0         ['input_1[0][0]']             
                                                                                                  
 tf.identity_3 (TFOpLambda)  (None, 96, 96, 3)            0         ['input_1[0][0]']             
                                                                                           

In [ ]:
from sklearn.metrics import mean_squared_error, confusion_matrix
# Ottenere le predizioni sul dataset di validazione
predictions = model.predict(np.copy(x_val))

# Compute the confusion matrix
cm = confusion_matrix(np.argmax(y_val, axis=-1), np.argmax(predictions, axis=-1))

# Plot the confusion matrix
plt.figure(figsize=(10, 8))
sns.heatmap(cm.T, xticklabels=list(('Healthy','Unhealthy')), yticklabels=list(('Healthy','Unhealthy')), cmap='Blues', annot=True)
plt.xlabel('True labels')
plt.ylabel('Predicted labels')
plt.show()

In [ ]:
# Save the best model
model.save('3Modelli_3')
del model